In [223]:
from nltk.corpus import wordnet as wn
import nltk 
import re
import math
import scipy
from nltk.corpus import semcor
import random

In [224]:
def remove_punctuation(sentence):
    return re.sub(r'[^\w\s]', '', str(sentence)).strip()

def get_stopwords():
    stopwords_file = open(f"./resources/utils/stop_words__frakes_baeza-yates.txt", "r")
    stopwords_list = []
    for word in stopwords_file:
        stopwords_list.append(word.replace('\n', ''))
    stopwords_file.close()

    stopwords_file = open(f"./resources/utils/stop_words_1.txt", "r")
    stopwords_list = []
    for word in stopwords_file:
        stopwords_list.append(word.replace('\n', ''))
    stopwords_file.close()

    stopwords_file = open(f"./resources/utils/stop_words_FULL.txt", "r")
    stopwords_list = []
    for word in stopwords_file:
        stopwords_list.append(word.replace('\n', ''))
    stopwords_file.close()
    
    stopwords_list = list(set(stopwords_list))

    return stopwords_list
     
def remove_stopwords(sentence, stopwords_list):
    return [word for word in sentence.split() if word not in stopwords_list]



### Esercitazione su Word Sense Disambiguation: 

#### INPUT : 
l’input per questa esercitazione è costituito da coppie di termini contenute nel file WordSim353 (disponibile nei
formati .tsv e .csv)
- Il file contiene 353 coppie di termini utilizzati come testset in varie competizioni internazionali
- A ciascuna coppia è attribuito un valore numerico [0,10], che rappresenta la similarità fra gli elementi della coppia.

In [225]:
import csv

sim_file = f"resources/WordSim353/WordSim353.csv"

pairs = []
with open(sim_file, 'r', encoding = "utf-8") as f:
    reader = csv.reader(f)
    reader.__next__()
    for lines in reader:
        pairs.append(lines)
    
print("WordSim353 correctly loaded!")


WordSim353 correctly loaded!


#### Prima parte

Implementare tre misure di similarità basate su WordNet. Per ciascuna delle misure di similarità, calcolare:
- gli indici di correlazione di Spearman e
- gli indici di correlazione di Pearson fra i risultati ottenuti e quelli ‘target’ presenti nel file annotato.

Le misure da implementare sono le seguenti: 
- Wu & Palmer: 
$$cs(s_1, s_2) = \frac{2 \cdot depth(LCS)}{depth(s_1) + depth(s_2)}$$

in cui $LCS$ rappresenta il primo antenato comune (Lowest Common Subsumer) e depth è la funzione che misura la distanza fra la radice di WordNet e il sysnet $x$. 

***L’obiettivo è implementare la misura di similarità di Wu & Palmer! Non dobbiamo fare ciò viene già fatto nell’implementazione di nltk o altre librerie!***



In [226]:
def get_LCS(sysnet1, sysnet2):
    hyperonyms1 = []
    hyperonyms2 = []

    hyperonyms1.append(sysnet1) # il primo elemento della lista è il synset da cui si parte, quindi la foglia
    hyperonyms2.append(sysnet2) # il primo elemento della lista è il synset da cui si parte, quindi la foglia

    # per ogni synset si prendono gli iperonimi e si aggiungono alla lista
    for synset in hyperonyms1:
        synset_hyp = synset.hypernyms()
        #print("\nPER ", str(synset), " GLI IPERONIMI SONO: ", synset_hyp)

        if synset_hyp:
            hyperonyms1.extend(synset_hyp)

    # per ogni synset si prendono gli iperonimi e si aggiungono alla lista
    for synset in hyperonyms2:
        synset_hyp = synset.hypernyms()
        if synset_hyp:
            hyperonyms2.extend(synset_hyp)

    for syn1 in hyperonyms1:
        for syn2 in hyperonyms2:
            # il primo synset che è in comune è il più basso (LCS )
            if syn1 == syn2:
                return syn1 #LCS: Lowest Common Subsumer

    return None

In [227]:
def type_check(list_of_synset):
    for syn in list_of_synset:
        if not isinstance(syn, nltk.corpus.reader.wordnet.Synset):
            raise TypeError("The input parameters must be Synset objects")
    return True

def wu_palmer_similarity(syn1, syn2):
    """
    Returns the Wu-Palmer similarity between synset.
    """

    if isinstance(syn1, nltk.corpus.reader.wordnet.Synset) and isinstance(syn2, nltk.corpus.reader.wordnet.Synset):
        print("\nSYN1: " + str(syn1))
        print("SYN2: " + str(syn2))
        LCS = get_LCS(syn1, syn2)
        print("LCS: " + str(LCS))

        lcs_depth = 0
        
        if LCS:
            lcs_depth = LCS.max_depth()

        # TODO: CAPIRE SE USARE MAX DEPTH O MIN DEPTH
        cs = (2 * (lcs_depth)) / ((syn1.max_depth()) + (syn2.max_depth()))
        
        print("WE PALMER SIMILARITY MANUAL")
        print(cs)

        print("WU PALMER SIMILARITY NLTK")
        print(syn1.wup_similarity(syn2))

        return cs
    else:
        raise TypeError("The input parameters must be Synset objects")

In [228]:
wu_palmer_similarity(wn.synsets("boat")[0], wn.synsets("computer")[0])


SYN1: Synset('boat.n.01')
SYN2: Synset('computer.n.01')
LCS: Synset('instrumentality.n.03')
WE PALMER SIMILARITY MANUAL
0.5555555555555556
WU PALMER SIMILARITY NLTK
0.6


0.5555555555555556

- Shortest Path:
$$sim_{path}(s_1, s_2) = 2 \cdot depthMax - len(s_1, s_2)$$

in cui $depthMax$ è un valore fissato per una specifica versione di WordNet. 

In [229]:
#CALCOLO REALE depthMax = max(max(len(hyp_path) for hyp_path in ss.hypernym_paths()) for ss in wn.all_synsets())
depth_max = 20

# TODO: CONTROLLARE QUA -> C'E' QUALCOSA DA SISTEMARE
def path_len_between_two_synset(synset1, synset2):
    LCS = get_LCS(synset1, synset2)
    print("LCS: ", LCS)
    print("LCS LIBRARY: ", synset1.lowest_common_hypernyms(synset2))
    if LCS is not None:
        print("synset1.max_depth(): ", synset1.max_depth())
        print("synset2.max_depth(): ", synset2.max_depth())
        print("LCS.max_depth(): ", LCS.max_depth())
        
        distance = (synset1.max_depth() - LCS.max_depth()) + (synset2.max_depth() - LCS.max_depth())
        print("DISTANCE: ", distance)
        print("DISTANCE LIBRARY: ", (synset1.shortest_path_distance(LCS) + synset2.shortest_path_distance(LCS)))

        return distance
    return 0

def shortest_path(synset1, synset2):
    return 2 * depth_max - path_len_between_two_synset(synset1, synset2)


In [230]:
shortest_path_value = shortest_path(wn.synsets("dog")[0], wn.synsets("computer")[0])
print(shortest_path_value)

wn.synsets("dog")[0].path_similarity(wn.synsets("cat")[0])

LCS:  Synset('whole.n.02')
LCS LIBRARY:  [Synset('whole.n.02')]
synset1.max_depth():  13
synset2.max_depth():  8
LCS.max_depth():  3
DISTANCE:  15
DISTANCE LIBRARY:  10
25


0.2

- Leakcock & Chodorow: 
$$sim_{LC}(s_1, s_2) = - log \frac{len(s_1, s_2)}{2 \cdot depthMax}$$

In [231]:
def leakcock_chodorow(synset1, synset2):
    fract = shortest_path(synset1, synset2) / (2 * depth_max)
    return - math.log(fract)

In [232]:
print("MANUAL: ", leakcock_chodorow(wn.synsets("dog")[0], wn.synsets("computer")[0]))

print("LIBRARY: ", wn.synsets("dog")[0].lch_similarity(wn.synsets("computer")[0]))

LCS:  Synset('whole.n.02')
LCS LIBRARY:  [Synset('whole.n.02')]
synset1.max_depth():  13
synset2.max_depth():  8
LCS.max_depth():  3
DISTANCE:  15
DISTANCE LIBRARY:  10
MANUAL:  0.4700036292457356
LIBRARY:  1.2396908869280152


#### Calcolo della similarità

Le funzioni precedentemente implementate richiedono come input sensi e non i termini. Quindi per calcolare la similarità fra 2 termini è necessario prendere la massima similarità fra tutti i sensi del primo termine e tutti i sensi del secondo termine. 

L'ipotesi quindi è che i due termini funzionino come contesto di disambiguazione l'uno per l'altro. 

L'equazione che formalizza questa idea è la seguente: 

$$sim(w_1, w_2) = \max_{c_1 \in s(w_1), c_2 \in s(w_2)} [sim(c_1, c_2)]$$

***NB!*** Per calcolare gli indici di correlazione non si è interessati a entrare nel merito di come sono calcolati, possiamo prendere delle funzioni prefatte e usarle.

In [233]:
def get_similarity():
    file = open(f'./resources/WordSim353/WordSim353.csv')
    type(file)
    file_rows = csv.reader(file)
    rows = []
    for row in file_rows:
        print("ROW: ", row)
        rows.append(row)
    file.close()

    rows.remove(rows[0]) # rimuovo l'header del vile csv
    print("ROWS: ", rows)

    #Contengono la somiglianza
    wordsimilarities = []
    wu_palmer_similarities = []
    shortpath_similarities = []
    leakcock_chodorow_similarities = []

    #Metriche
    for row in rows:
        print("-------------------------------")
        print(row)
        term1 = row[0]
        term2 = row[1]

        print(term1)
        print(term2)
        synsets1 = wn.synsets(term1)
        synsets2 = wn.synsets(term2)

        try:
            print("\nsynsets1: ", synsets1)
            print("synsets2: ", synsets2)
            
            if (synsets1 != [] and synsets2 != []):

                wu_palmer_max = 0
                short_path_max = 0
                leakcock_chodorow_max = 0

                for s1 in synsets1:
                    for s2 in synsets2:

                        # Metrica 1
                        print("Wu palmer")
                        wu_palmer = wu_palmer_similarity(s1, s2)
                        # print(wu_palmer_nltk(synset1,synset2))

                        if wu_palmer > wu_palmer_max:
                            wu_palmer_max = wu_palmer

                        #Metrica 2
                        #print(shortest_path(s1, s2))
                        # print(shortest_path_nltk(synset1, synset2))
                        shortpath = shortest_path(s1, s2)

                        if shortpath > short_path_max:
                            short_path_max = shortpath

                        # Metrica 3
                        print("Leakcock & Chodorow")
                        #print(math.log(2*(max(max(len(hyp_path) for hyp_path in ss.hypernym_paths()) for ss in wn.all_synsets()))+1))
                        leacchod = leakcock_chodorow(s1, s2)
                        # print(leakcockchodrow_nltk(synset1,synset2))

                        if leacchod > leakcock_chodorow_max:
                            leakcock_chodorow_max = leacchod

                wu_palmer_similarities.append(float(wu_palmer_max))
                shortpath_similarities.append(float(short_path_max))
                leakcock_chodorow_similarities.append(float(leakcock_chodorow_max))
                
                wordsimilarities.append(float(row[2]))

                
        except:
            print("Errore elemento in wordnet")

    return wu_palmer_similarities, shortpath_similarities, leakcock_chodorow_similarities, wordsimilarities

In [234]:
wupalmerres, pathres, lcres, wordsimres = get_similarity()

ROW:  ['Word 1', 'Word 2', 'Human (mean)']
ROW:  ['love', 'sex', '6.77']
ROW:  ['tiger', 'cat', '7.35']
ROW:  ['tiger', 'tiger', '10.00']
ROW:  ['book', 'paper', '7.46']
ROW:  ['computer', 'keyboard', '7.62']
ROW:  ['computer', 'internet', '7.58']
ROW:  ['plane', 'car', '5.77']
ROW:  ['train', 'car', '6.31']
ROW:  ['telephone', 'communication', '7.50']
ROW:  ['television', 'radio', '6.77']
ROW:  ['media', 'radio', '7.42']
ROW:  ['drug', 'abuse', '6.85']
ROW:  ['bread', 'butter', '6.19']
ROW:  ['cucumber', 'potato', '5.92']
ROW:  ['doctor', 'nurse', '7.00']
ROW:  ['professor', 'doctor', '6.62']
ROW:  ['student', 'professor', '6.81']
ROW:  ['smart', 'student', '4.62']
ROW:  ['smart', 'stupid', '5.81']
ROW:  ['company', 'stock', '7.08']
ROW:  ['stock', 'market', '8.08']
ROW:  ['stock', 'phone', '1.62']
ROW:  ['stock', 'CD', '1.31']
ROW:  ['stock', 'jaguar', '0.92']
ROW:  ['stock', 'egg', '1.81']
ROW:  ['fertility', 'egg', '6.69']
ROW:  ['stock', 'live', '3.73']
ROW:  ['stock', 'life', '0.

In [235]:
#Indici di correlazione

print("len(wordsimres): ", len(wordsimres))
print("len(wupalmerres): ", len(wupalmerres))
print("len(pathres): ", len(pathres))
print("len(lcres): ", len(lcres))

#Pearson
print("####################################################################")
print("Pearson ")
print(scipy.stats.pearsonr(wordsimres, wupalmerres))
print(scipy.stats.pearsonr(wordsimres, pathres))
print(scipy.stats.pearsonr(wordsimres, lcres))

#Spearman
print("Spearman ")
print(scipy.stats.spearmanr(wordsimres, wupalmerres))
print(scipy.stats.spearmanr(wordsimres, pathres))
print(scipy.stats.spearmanr(wordsimres, lcres))

len(wordsimres):  344
len(wupalmerres):  344
len(pathres):  344
len(lcres):  344
####################################################################
Pearson 
PearsonRResult(statistic=0.2875552825016864, pvalue=5.6659870640326836e-08)
PearsonRResult(statistic=0.052050484263076305, pvalue=0.33578272369863066)
PearsonRResult(statistic=-0.13393690226297567, pvalue=0.012906826915260605)
Spearman 
SpearmanrResult(correlation=0.3345009240506682, pvalue=1.9429120468873036e-10)
SpearmanrResult(correlation=-0.007033709540952225, pvalue=0.8965801528448636)
SpearmanrResult(correlation=-0.1352447411891635, pvalue=0.012044691049485745)


### Seconda parte

Implementare l’algoritmo di Lesk (NON (!=) usare implementazione esistente, e.g., in nltk…).
1. Estrarre 50 frasi dal corpus SemCor (corpus annotato con i synset di
WN) e disambiguare (almeno) un sostantivo per frase. 
Calcolare l’accuratezza del sistema implementato sulla base dei sensi annotati in
SemCor.
    - SemCor è disponibile all’URL http://web.eecs.umich.edu/~mihalcea/downloads.html
2. Randomizzare la selezione delle 50 frasi e la selezione del termine da disambiguare, 
e restituire l’accuratezza media su (per esempio) 10 esecuzioni del programma.

In [236]:
stop_words = get_stopwords()

In [237]:
def get_set_of_words(phrase):
    """
    Returns the set of words of a phrase.
    """
    phrase = remove_punctuation(phrase)
    set_of_words = remove_stopwords(phrase, stop_words)
    
    return set_of_words

In [238]:
def get_context_of_phrase(sentence):
    """
    Returns the context of a phrase.
    """
    sentence = remove_punctuation(sentence)
    set_of_words = remove_stopwords(sentence, stop_words)
    return set_of_words

def compute_overlap(signature, context):
    """
    returns the number of words in common between signature and context
    """

    number_of_words_in_common = len(list(set(signature) & set(context)))

    return number_of_words_in_common

def get_signature(synset):
    """
    returns the signature of synset
    """

    gloss_of_synset = synset.definition() #gloss of synset
    examples_of_synset = synset.examples() #examples of synset

    initial_signature = [gloss_of_synset] + examples_of_synset

    signature = []
    for phrase in initial_signature:
        set_of_words = get_set_of_words(phrase)
        signature.append(set_of_words)

    result = sum(signature, []) # flatten list of lists
    return list(set(result)) # remove duplicates

def lesk(word, sentence):
    """
    returns best sense of word
    """

    best_sense = None #most frequent sense for word

    max_overlap = 0
    context = sentence #get_context_of_phrase(sentence) #set of words in sentence
    
    for synset in wn.synsets(word):
        # TODO: CAPIRE QUALE SIGNATURE USARE -> SE USIAMO A PRIMA VENGONO TROVATI MENO SYNSET DAL LESK, ALTRIMENTI DI PIU'

        signature = get_signature(synset) #set of words in the gloss and examples of sense
        # signature = synset.definition().split()

        overlap = compute_overlap(signature, context)

        if overlap > max_overlap:
            max_overlap = overlap
            best_sense = synset

    return best_sense

In [239]:
best_sense = lesk("dog", "I saw a dog in the park")

print("best sense:")
print(best_sense) 

best sense:
None


In [240]:
def lemma_list(sent):
    return [l.label() if isinstance(l, nltk.tree.Tree) else None for l in sent]

def part_two_first_50_phrases():  # implementazione del primo punto della seconda parte, con l'utilizzo delle prime 50 frasi del corpus semcor
    d = semcor.sents()
    sentences = d[0:50]

    lesk_correct = 0 # numero di volte che lesk ha trovato la giusta definizione

    for i in range(0,50): # per ogni frase
        print("-------------")
        print("sentences[i]: ", sentences[i])

        print("\nTAGGED")

        print(semcor.tagged_sents(tag="sem")[i], "\n\n")
        
        # recupero i lemmi dalla frase taggata con il synset per ogni parola
        lemma = lemma_list(semcor.tagged_sents(tag="sem")[i]) # :param tag: `'pos'` (part of speech), `'sem'` (semantic), or `'both'`
        print(lemma)

        print("FINE STAMPA LEMMA")

        lemma_length = len(lemma)
        found = False #quando trovo un nome mi fermo
        
        j = 0
        while (j < lemma_length and found == False):
            if (str(lemma[j]) != 'None'):
                string = str(lemma[j])
                string = string.replace("Lemma('","")
                string = string.replace("')", "") # jury.n.01.jury
                synset_string = string.rsplit('.', 1)[0]

                parts = string.split('.')   # jury.n.01.jury --> ['jury', 'n', '01', 'jury']
                
                # Lemma('jury.n.01.jury') --> "synset".paroladeltesto
                # parts[0] = jury
                # parts[1] = n (può essere 'n', 'r', 'v', ...)
                # parts[2] = 01
                # parts[3] = jury # lemma della parola del testo che ha "taggato"

                if (parts[1] == 'n' and parts[3] in sentences[i]): # PRIMA C'ERA ANCHE :  and len(parts) > 3
                    found = True
                    lesk_synset = lesk(parts[3],sentences[i]) # trovo il synset con lesk
                    print(sentences[i])
                    print("Word: "+parts[3])
                    print("Lesk algorithm: " + str(lesk_synset))
                    print(parts[0],parts[1],parts[2]) 

                    syn = str(lesk_synset)
                    if (syn != None):
                        syn = syn.replace("Synset('", "")
                        syn = syn.replace("')","")

                        if (synset_string == syn): # confronto il synset trovato con lesk con quello "taggato" nel testo
                            lesk_correct = lesk_correct + 1

            j = j+1
        lemma.clear()

    print("numero di volte che lesk ha trovato la giusta definizione: " + str(lesk_correct))

In [241]:
part_two_first_50_phrases()

-------------
sentences[i]:  ['The', 'Fulton', 'County', 'Grand', 'Jury', 'said', 'Friday', 'an', 'investigation', 'of', 'Atlanta', "'s", 'recent', 'primary', 'election', 'produced', '``', 'no', 'evidence', "''", 'that', 'any', 'irregularities', 'took', 'place', '.']

TAGGED
[['The'], Tree(Lemma('group.n.01.group'), [Tree('NE', ['Fulton', 'County', 'Grand', 'Jury'])]), Tree(Lemma('state.v.01.say'), ['said']), Tree(Lemma('friday.n.01.Friday'), ['Friday']), ['an'], Tree(Lemma('probe.n.01.investigation'), ['investigation']), ['of'], Tree(Lemma('atlanta.n.01.Atlanta'), ['Atlanta']), ["'s"], Tree(Lemma('late.s.03.recent'), ['recent']), Tree(Lemma('primary.n.01.primary_election'), ['primary', 'election']), Tree(Lemma('produce.v.04.produce'), ['produced']), ['``'], ['no'], Tree(Lemma('evidence.n.01.evidence'), ['evidence']), ["''"], ['that'], ['any'], Tree(Lemma('abnormality.n.04.irregularity'), ['irregularities']), Tree(Lemma('happen.v.01.take_place'), ['took', 'place']), ['.']] 


[None, Le

In [242]:
def gen_random_numbers_in_range(low, high, n):
    return random.sample(range(low, high), n)

In [243]:
def part_two_random_phrases():  # implementazione del secondo punto della seconda parte, con l'utilizzo di 50 frasi casuali del corpus semcor
    d = semcor.sents()
    index_list = gen_random_numbers_in_range(0, len(d), 50) # genero 50 numeri casuali tra 0 e il numero di frasi nel corpus

    sentences = [d[i] for i in index_list]  # prendo 50 frasi casuali

    lesk_correct = 0 # numero di volte che lesk ha trovato la giusta definizione

    for i in range(0,50): # per ogni frase
        print("-------------")
        print("sentences[i]: ", sentences[i])

        print("\nTAGGED")

        print(semcor.tagged_sents(tag="sem")[i], "\n\n")
        
        # recupero i lemmi dalla frase taggata con il synset per ogni parola
        lemma = lemma_list(semcor.tagged_sents(tag="sem")[i]) # :param tag: `'pos'` (part of speech), `'sem'` (semantic), or `'both'`
        print(lemma)

        print("FINE STAMPA LEMMA")

        lemma_length = len(lemma)
        noun_list = []

        j = 0
        while (j < lemma_length):
            if (str(lemma[j]) != 'None'):
                string = str(lemma[j])
                string = string.replace("Lemma('","")
                string = string.replace("')", "") # jury.n.01.jury
                synset_string = string.rsplit('.', 1)[0]

                parts = string.split('.')   # jury.n.01.jury --> ['jury', 'n', '01', 'jury']
                
                # Lemma('jury.n.01.jury') --> "synset".paroladeltesto
                # parts[0] = jury
                # parts[1] = n (può essere 'n', 'r', 'v', ...)
                # parts[2] = 01
                # parts[3] = jury # lemma della parola del testo che ha "taggato"

                if (parts[1] == 'n' and parts[3] in sentences[i]):

                    noun_list.append([parts[0], parts[1], parts[2], parts[3]]) # aggiungo alla lista dei nomi la parola, il suo synset e il lemma

            j = j+1

        print("NOUN_LIST: ", noun_list)
        print("LEN(NOUN_LIST): ", len(noun_list))

        if len(noun_list) > 0:
            selected_noun = random.choice(noun_list) # seleziono un nome a caso tra quelli presenti nella frase
            print("\nSELECTED_NOUN: ", selected_noun, "\n")

            lesk_synset = lesk(selected_noun[3], sentences[i]) # trovo il synset con lesk
            print(sentences[i])
            print("Word: "+selected_noun[3])
            print("Lesk algorithm: " + str(lesk_synset))
            print(selected_noun[0],selected_noun[1],selected_noun[2]) 

            syn = str(lesk_synset)
            if (syn != None):
                syn = syn.replace("Synset('", "")
                syn = syn.replace("')","")

                if (synset_string == syn): # confronto il synset trovato con lesk con quello "taggato" nel testo
                    lesk_correct = lesk_correct + 1

        lemma.clear()
        noun_list.clear()

    print("numero di volte che lesk ha trovato la giusta definizione: " + str(lesk_correct))

In [244]:
part_two_random_phrases()

-------------
sentences[i]:  ['There', ',', 'Mother', 'was', 'received', 'by', 'the', 'scions', 'of', 'aristocratic', 'lines', 'which', 'are', 'dominated', 'by', 'the', 'Budweisers', '(', 'of', 'beer', 'derivation', ')', ',', 'the', 'Chalmers', '(', 'of', 'underwear', 'origin', ')', ',', 'and', 'the', 'Heinzes', '(', 'whose', 'forbears', 'founded', 'a', 'nationally', 'famous', 'trade', 'in', 'pickles', ')', '.']

TAGGED
[['The'], Tree(Lemma('group.n.01.group'), [Tree('NE', ['Fulton', 'County', 'Grand', 'Jury'])]), Tree(Lemma('state.v.01.say'), ['said']), Tree(Lemma('friday.n.01.Friday'), ['Friday']), ['an'], Tree(Lemma('probe.n.01.investigation'), ['investigation']), ['of'], Tree(Lemma('atlanta.n.01.Atlanta'), ['Atlanta']), ["'s"], Tree(Lemma('late.s.03.recent'), ['recent']), Tree(Lemma('primary.n.01.primary_election'), ['primary', 'election']), Tree(Lemma('produce.v.04.produce'), ['produced']), ['``'], ['no'], Tree(Lemma('evidence.n.01.evidence'), ['evidence']), ["''"], ['that'], ['an